In [65]:
import pandas as pd
import plotly.graph_objects as go
from IPython.display import display

from src.constants import STATIONS

fig = go.Figure()
for station in [STATIONS[2], STATIONS[1], STATIONS[9]]:
  filename = f'data_cleaned/{station}_observations.csv'
  dataframe = pd.read_csv(filename, parse_dates=['timestamp']).dropna()

  without_zeroes = dataframe[dataframe['ghi'] > 0]
  fig.add_trace(go.Histogram(x=without_zeroes['ghi'], name=station, autobinx=False, xbins=(dict(size=25))))
  fig.update_layout(title=f'Selected Measurement Point GHI Histogram', height=400, width=600, barmode='overlay')
  fig.update_yaxes(range=[0, 3500])
  fig.update_xaxes(range=[0, 1200])
  fig.update_traces(opacity=.60)
fig.show()

fig = go.Figure()
for station in [STATIONS[2], STATIONS[1], STATIONS[9]]:
  filename = f'data_cleaned/{station}_observations.csv'
  dataframe = pd.read_csv(filename, parse_dates=['timestamp']).dropna()
  four_days = dataframe[(dataframe['timestamp'] > '2021-06-01 06:00') & (dataframe['timestamp'] < '2021-06-05 06:00')]
  fig.add_trace(go.Scatter(x=four_days['timestamp'], y=four_days['ghi'], name=station))
fig.update_layout(height=400, width=600, title='Selected Measurement Points GHI')
fig.show()

for station in [STATIONS[2]]:
  one_year = dataframe[(dataframe['timestamp'] > '2020-11-01 06:00') & (dataframe['timestamp'] < '2021-11-01 06:00')]
  fig = go.Figure()
  fig.add_trace(go.Scatter(x=one_year['timestamp'], y=one_year['ghi']))
  fig.update_layout(height=400, width=600, title='Yearly GHI Hanford CA')
  fig.show()



In [25]:

import pandas as pd
import numpy as np
import math
import plotly.graph_objects as go
from src.generate_features import generate_harmonic_historical_features, generate_historical_features, generate_persistence_fcst, historical_feature
from src.constants import STATIONS, HOURS_AHEAD, HOURS_HX, HOURS_FORECASTED, HARMONIC_FEATURES
from src.models import build_and_train_model_validation_early_stop
from sklearn.preprocessing import MinMaxScaler

sample_filename = f'data_cleaned/{STATIONS[0]}_observations.csv'
sample_dataframe = pd.read_csv(sample_filename, parse_dates=['timestamp'])

additional_weather_features = set(sample_dataframe.columns).difference(['timestamp', 'ghi'])
  
all_features = ['ghi'] + list(additional_weather_features) 
## Prepare dataframe, with boxed values for historical data
dataframe = generate_historical_features(sample_dataframe, hours_ahead=HOURS_AHEAD, hours_history=HOURS_HX, hours_forecasted=HOURS_FORECASTED, features=all_features)
dataframe = generate_harmonic_historical_features(dataframe, hours_ahead=HOURS_AHEAD, hours_history=HOURS_HX)
dataframe = generate_persistence_fcst(dataframe, hours_ahead=HOURS_AHEAD, hours_forecasted=HOURS_FORECASTED).dropna()

## Partition Dataset
train_set = dataframe[dataframe['timestamp'].dt.year < 2021]
validation_set = dataframe[dataframe['timestamp'].dt.year >= 2021]

feature_list = all_features + HARMONIC_FEATURES
num_features = len(feature_list) 
selected_features = [historical_feature(feature, i+HOURS_AHEAD) for i in range(HOURS_HX) for feature in feature_list]
num_neurons = 48
target_columns = [f'ghi_actual_{i}' for i in range(HOURS_FORECASTED)]

## Initialize scalers
feature_scaler = MinMaxScaler(feature_range=(0,1))
target_scaler = MinMaxScaler(feature_range=(0,1))

## Scale train set features
training_inputs = np.array(train_set.loc[:,selected_features].values)
feature_scaler = feature_scaler.fit(training_inputs)
scaled_training_inputs = feature_scaler.transform(training_inputs)
scaled_training_inputs = scaled_training_inputs.reshape(len(training_inputs), HOURS_HX, num_features)

## Scale train set outputs
training_data_targets = train_set.loc[:,target_columns]
target_scaler = target_scaler.fit(training_data_targets)
scaled_train_targets = target_scaler.transform(training_data_targets)

validation_features = np.array(validation_set.loc[:,selected_features].values)
scaled_validation_features = feature_scaler.transform(validation_features)
scaled_validation_features = scaled_validation_features.reshape(len(validation_set), HOURS_HX, num_features)

validation_true_values = validation_set.loc[:,target_columns]
scaled_validation_targets = target_scaler.transform(validation_true_values)

num_epochs=250
## Train Model
model, history = build_and_train_model_validation_early_stop( \
  train_features=scaled_training_inputs, 
  train_targets=scaled_train_targets, 
  num_neurons=num_neurons, 
  num_layers=2, 
  num_epochs=num_epochs, 
  num_features=num_features,
  verbose=2,
  patience=15,
  )

fig = go.Figure()
x=[x for x in range(num_epochs)]
fig.add_trace(go.Scatter(x=x, y=history.history['loss'], name="Training MSE"))
fig.add_trace(go.Scatter(x=x, y=history.history['val_loss'], name="Validation MSE"))
fig.update_layout(height=600, width=800, title="Forecast Overfitting Example")
fig.show()

Epoch 1/250
486/486 - 15s - loss: 0.0196 - mse: 0.0196 - val_loss: 0.0153 - val_mse: 0.0153
Epoch 2/250
486/486 - 11s - loss: 0.0145 - mse: 0.0145 - val_loss: 0.0105 - val_mse: 0.0105
Epoch 3/250
486/486 - 11s - loss: 0.0077 - mse: 0.0077 - val_loss: 0.0061 - val_mse: 0.0061
Epoch 4/250
486/486 - 11s - loss: 0.0065 - mse: 0.0065 - val_loss: 0.0060 - val_mse: 0.0060
Epoch 5/250
486/486 - 11s - loss: 0.0064 - mse: 0.0064 - val_loss: 0.0060 - val_mse: 0.0060
Epoch 6/250
486/486 - 11s - loss: 0.0064 - mse: 0.0064 - val_loss: 0.0060 - val_mse: 0.0060
Epoch 7/250
486/486 - 11s - loss: 0.0063 - mse: 0.0063 - val_loss: 0.0060 - val_mse: 0.0060
Epoch 8/250
486/486 - 11s - loss: 0.0063 - mse: 0.0063 - val_loss: 0.0059 - val_mse: 0.0059
Epoch 9/250
486/486 - 11s - loss: 0.0063 - mse: 0.0063 - val_loss: 0.0059 - val_mse: 0.0059
Epoch 10/250
486/486 - 11s - loss: 0.0062 - mse: 0.0062 - val_loss: 0.0061 - val_mse: 0.0061
Epoch 11/250
486/486 - 11s - loss: 0.0062 - mse: 0.0062 - val_loss: 0.0060 - va

In [66]:
from sklearn.metrics import mean_squared_error
test_features = np.array(validation_set.loc[:,selected_features].values)
scaled_test_features = feature_scaler.transform(test_features)
scaled_test_features = scaled_test_features.reshape(len(validation_set), HOURS_HX, num_features)

model_predictions = model.predict(scaled_test_features)
model_predictions_unscaled = target_scaler.inverse_transform(model_predictions)

test_true_values = validation_set.loc[:,target_columns]

rmse_for_model = math.sqrt(mean_squared_error(y_true=test_true_values, y_pred=model_predictions_unscaled))

persistence_targets = [f'ghi_persistence_fcst_{i}' for i in range(HOURS_FORECASTED)]
persistence_predictions = validation_set.loc[:,persistence_targets]
rmse_for_persistence= math.sqrt(mean_squared_error(y_true=test_true_values, y_pred=persistence_predictions))

print(f'Persistence Accuracy: {rmse_for_persistence}, \t Model Accuracy: {rmse_for_model}')

model_predictions_unscaled = pd.DataFrame(model_predictions_unscaled, columns=test_true_values.columns)

y_max = max(dataframe['ghi']) * 1.10

for i in range(10):
  offset=8
  index = (i*24) + offset
  true_values = test_true_values.iloc[index,:]
  pers_values = persistence_predictions.iloc[index,:]
  model_values = model_predictions_unscaled.iloc[index,:]

  x_values = [x for x in range(len(test_true_values))]
  fig = go.Figure()
  fig.add_trace(go.Scatter(x=x_values, y=true_values, name='Actual'))
  fig.add_trace(go.Scatter(x=x_values, y=pers_values, name='Persistence'))
  fig.add_trace(go.Scatter(x=x_values, y=model_values, name='Model'))
  fig.update_yaxes(range=[0,y_max])
  fig.update_layout(title=f'Index {index} forecast', height=400, width=600)
  fig.show()

Persistence Accuracy: 120.56930830830022, 	 Model Accuracy: 97.7960524997717


In [21]:
import pandas as pd
import numpy as np
import math as math
import tensorflow as tf
import tensorflow.keras as keras
import scipy.stats as stats
from src.generate_features import generate_historical_features, generate_harmonic_historical_features, generate_persistence_fcst, historical_feature
from src.constants import HOURS_AHEAD, HOURS_FORECASTED, HOURS_HX, HARMONIC_FEATURES
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_squared_error

df = pd.read_csv('src/accumulated_results.csv')
features = df['Features'].unique()

min_values = df.groupby(by=['Station', 'Features'])['Model_Performance'].idxmin()
min_value_df = df.iloc[min_values]
min_value_df.to_csv('best_results.csv')

min_value_df.loc[:,'Error_Reduction'] = ((min_value_df.loc[:,'Persistence_Performance'] - min_value_df.loc[:,'Model_Performance'])/min_value_df.loc[:,'Persistence_Performance'])

def get_used_weather_features(station, feature_string, iteration):
  '''
  The set difference of terms doesn't preserve order; so results were incorrect as re-building the inputs was ordering the additional weather differently.
  This function retrieves the original parameter order for all features from the associated model's logging, to ensure the same order when re-calculating error here for statistical testing.
  '''
  summary_file_name = f'logs/{station}_{feature_string}_{iteration}_summary.txt'
  with open(summary_file_name) as f:
    lines = f.readlines()
    line = lines[2]
    just_list = line[9:len(line)]
    new_list = just_list.replace('[', '').replace(']','').replace("'", '').replace(',', '').replace('\t', '').replace('\n', '') # There's definitely a better way to do this but this worked.
    return new_list.split(' ')

def get_data(station, feature_string, iteration):
  filename = f'data_cleaned/{station}_observations.csv'
  dataframe = pd.read_csv(filename, parse_dates=['timestamp'])
  additional_weather_features = set(dataframe.columns).difference(['timestamp', 'ghi'])

  all_features = ['ghi'] + list(additional_weather_features)
  ## Prepare dataframe, with boxed values for historical data
  dataframe = generate_historical_features(dataframe, hours_ahead=HOURS_AHEAD, hours_history=HOURS_HX, hours_forecasted=HOURS_FORECASTED, features=all_features)
  dataframe = generate_harmonic_historical_features(dataframe, hours_ahead=HOURS_AHEAD, hours_history=HOURS_HX)
  dataframe = generate_persistence_fcst(dataframe, hours_ahead=HOURS_AHEAD, hours_forecasted=HOURS_FORECASTED).dropna()
  
  ## Partition Dataset
  train_set = dataframe[dataframe['timestamp'].dt.year < 2021]
  test_set = dataframe[dataframe['timestamp'].dt.year >= 2021]

  features_used = get_used_weather_features(station, feature_string, iteration)
  selected_features = [historical_feature(feature, i+HOURS_AHEAD) for i in range(HOURS_HX) for feature in features_used]

  ## Select output columns
  target_columns = [f'ghi_actual_{i}' for i in range(HOURS_FORECASTED)]

  ## Initialize scalers
  feature_scaler = MinMaxScaler(feature_range=(0,1))
  target_scaler = MinMaxScaler(feature_range=(0,1))

  ## Scale train set features
  training_inputs = np.array(train_set.loc[:,selected_features].values)
  feature_scaler = feature_scaler.fit(training_inputs)

  ## Scale train set outputs
  training_data_targets = train_set.loc[:,target_columns]
  target_scaler = target_scaler.fit(training_data_targets)

   ## Evaluate Performance on Test Set
  test_features = np.array(test_set.loc[:,selected_features].values)
  scaled_test_features = feature_scaler.transform(test_features)
  scaled_test_features = scaled_test_features.reshape(len(test_set), HOURS_HX, len(features_used))
  test_true_values = test_set.loc[:,target_columns]
  persistence_targets = [f'ghi_persistence_fcst_{i}' for i in range(HOURS_FORECASTED)]
  persistence_predictions = test_set.loc[:,persistence_targets]

  return scaled_test_features, target_scaler, test_true_values, persistence_predictions    


def calculate_p_value(row):
  station, features, iteration = row['Station'], row['Features'], row['Iteration']
  model = tf.keras.models.load_model(f'models/{station}_{features}_{iteration}/{station}_{features}_{iteration}_model.mdl')
  scaled_test_features, target_scaler, test_target_data, persistence_predictions = get_data(station, features, iteration) 
  
  scaled_output = model.predict(scaled_test_features)
  unscaled_model_output = target_scaler.inverse_transform(scaled_output)

  model_rmse = math.sqrt(mean_squared_error(y_true=test_target_data, y_pred=unscaled_model_output))
  persistence_rmse = math.sqrt(mean_squared_error(y_true=test_target_data, y_pred=persistence_predictions))
  print(station, features, iteration, f'Model RMSE: {model_rmse}, Persistence RMSE: {persistence_rmse}')

  model_error = np.array(test_target_data) - np.array(unscaled_model_output) 
  persistence_error = np.array(test_target_data) - np.array(persistence_predictions)

  model_square_error = np.square(model_error).flatten()
  persistence_square_error = np.square(persistence_error).flatten()

  (stat, pvalue) = stats.wilcoxon(x=persistence_square_error, y=model_square_error, alternative='greater')
  return pvalue

print(min_value_df)
min_value_df['p_value'] = min_value_df.apply(lambda row: calculate_p_value(row), axis=1)
min_value_df.to_csv('best_results.csv')



C:\Users\matth\AppData\Local\Temp\ipykernel_41888\4132625713.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  min_value_df.loc[:,'Error_Reduction'] = ((min_value_df.loc[:,'Persistence_Performance'] - min_value_df.loc[:,'Model_Performance'])/min_value_df.loc[:,'Persistence_Performance'])


     Unnamed: 0                                        Station  \
49           49                                   Bondville IL   
110         110                                   Bondville IL   
108         108                                   Bondville IL   
106         106                               Goodwin Creek MS   
47           47                               Goodwin Creek MS   
45           45                               Goodwin Creek MS   
37           37                             Hanford California   
8             8                             Hanford California   
36           36                             Hanford California   
118         118                                   Millbrook NY   
119         119                                   Millbrook NY   
117         117                                   Millbrook NY   
31           31  Natural Energy Laboratory of Hawaii Authority   
2             2  Natural Energy Laboratory of Hawaii Authority   
0         

C:\Users\matth\AppData\Local\Temp\ipykernel_41888\4132625713.py:100: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  min_value_df['p_value'] = min_value_df.apply(lambda row: calculate_p_value(row), axis=1)
